In [ ]:
!pip install datasets pandas
!pip install transformers

  Using cached datasets-3.2.0-py3-none-any.whl.metadata (20 kB)
  Using cached pandas-2.2.3-cp311-cp311-win_amd64.whl.metadata (19 kB)
  Using cached pyarrow-19.0.0-cp311-cp311-win_amd64.whl.metadata (3.4 kB)
  Using cached dill-0.3.8-py3-none-any.whl.metadata (10 kB)
  Using cached xxhash-3.5.0-cp311-cp311-win_amd64.whl.metadata (13 kB)
  Using cached multiprocess-0.70.16-py311-none-any.whl.metadata (7.2 kB)
  Using cached fsspec-2024.9.0-py3-none-any.whl.metadata (11 kB)
  Using cached aiohttp-3.11.11-cp311-cp311-win_amd64.whl.metadata (8.0 kB)
  Using cached tzdata-2025.1-py2.py3-none-any.whl.metadata (1.4 kB)
  Using cached aiohappyeyeballs-2.4.4-py3-none-any.whl.metadata (6.1 kB)
  Using cached aiosignal-1.3.2-py2.py3-none-any.whl.metadata (3.8 kB)
  Using cached attrs-25.1.0-py3-none-any.whl.metadata (10 kB)
  Using cached frozenlist-1.5.0-cp311-cp311-win_amd64.whl.metadata (14 kB)
  Using cached multidict-6.1.0-cp311-cp311-win_amd64.whl.metadata (5.1 kB)
  Using cached propcache

In [408]:
from datasets import load_dataset
import json
from transformers import pipeline
import torch
import os

Use the below cell, to change values for the experiment, after changing this run all the cells below 

In [3]:
dataset_name = "ai4privacy/pii-masking-200k"

In [667]:
samples = 10

In [412]:
#parameters for ollama experiment
source_text_file_name = "source_texts.json"
predicted_labels_file_name = "predicted_labels.json"
model_name =  "llama3.2:latest" #"qwen2.5:3b" #"llama3.2:latest"

In [413]:
results_with_labels_file_name = "results_with_labels_compared.json"
results_file_name = "results.json"


In [7]:
def load_data(dataset_name):
    dataset = load_dataset(dataset_name)
    filtered_dataset = dataset.filter(lambda example: example['language'] == 'en')
    df = filtered_dataset['train'].to_pandas() 
    df.head()
    return df


In [8]:

df = load_data(dataset_name=dataset_name)


In [457]:
#length of the dataset
len(df)

43501

In [668]:
def filtered_dataset(rows, df):
    return df.head(rows)

In [669]:
df_filtered = filtered_dataset(samples, df)

In [670]:
#length of filtered dataset
len(df_filtered)

10

In [671]:
print(df_filtered.iloc[4]['privacy_mask']) 

[{'value': '88', 'start': 4, 'end': 6, 'label': 'AGE'}
 {'value': '5862', 'start': 20, 'end': 24, 'label': 'BUILDINGNUMBER'}
 {'value': 'Y2rWliOhf8Ir', 'start': 98, 'end': 110, 'label': 'PASSWORD'}]


In [672]:
def extract_sensitive_data(privacy_mask):
    return {item['label']: item['value'] for item in privacy_mask}

In [673]:
df_filtered['sensitive_data_json'] = df_filtered['privacy_mask'].apply(extract_sensitive_data)

C:\Users\neham\AppData\Local\Temp\ipykernel_18760\1344952930.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_filtered['sensitive_data_json'] = df_filtered['privacy_mask'].apply(extract_sensitive_data)


In [674]:
df['sensitive_data_json'] = df['privacy_mask'].apply(extract_sensitive_data)

In [675]:
len(df_filtered)

10

In [676]:
print(df_filtered.iloc[4]['sensitive_data_json'])  #example of the new column generated

{'AGE': '88', 'BUILDINGNUMBER': '5862', 'PASSWORD': 'Y2rWliOhf8Ir'}


In [677]:
def collect_source_texts(data, file_name):
    source_texts = data['source_text'].tolist()
    with open(file_name, "w") as json_file:
        json.dump(source_texts, json_file)

In [678]:
collect_source_texts(df_filtered, source_text_file_name)

In [679]:
len(df_filtered)

10

In [680]:
source_text_file_name

'source_texts.json'

In [683]:
import json

def retrieve_source_texts(file_name):
    with open(file_name, "r") as json_file:
        source_texts = json.load(json_file)
    return source_texts

def count_source_texts(file_name):
    source_texts = retrieve_source_texts(file_name)
    return len(source_texts)

# Example usage
file_name = "source_texts.json"
source_text_count = count_source_texts(file_name)
print(f"Number of source texts: {source_text_count}")


Number of source texts: 10


Experimenting with Ollama, now run 'evaluation.js' to get the labels from the model (predicted labels by the model)

In [520]:
def get_predicted_labels(file_name):
    with open(file_name, 'r', encoding='utf-8') as file:
        data = json.load(file)  # Load the entire JSON object

    # Extract results and average processing time
    raw_results = data.get("results", [])  # Default to empty list if missing
    total_time = float(data.get("processingTimeSeconds", 0))  # Convert string to float
    average_time_per_prompt = float(data.get("averageTimePerPromptSeconds", 0))

    # Convert JSON strings into dictionaries
    parsed_results = []
    for item in raw_results:
        if item is not None:  
            try:
                parsed_results.append(json.loads(item))
            except json.JSONDecodeError:
                print(f"Invalid JSON detected, storing as empty object: {item}")
                parsed_results.append({})
        else:
            print("Null item found, storing as empty object")
            parsed_results.append({})

    return parsed_results, total_time, average_time_per_prompt

In [521]:
predicted_labels_file_name

'predicted_labels.json'

In [522]:
predicted_labels, total_time, average_time_per_prompt = get_predicted_labels(predicted_labels_file_name)

Null item found, storing as empty object


In [523]:
print(predicted_labels)

[{'IMEI': '06-184755-866851-3'}, {'name': 'Omer', 'identity document': 'license', 'type': '78B5R2MVFAHJ48500'}, {'age': '72', 'city': 'Intersex', 'height': '158centimeters'}, {'name': 'Nancy', 'age': '18', 'city': 'Boston', 'place': '16356', 'key': '5890724654311332'}, {'age': '88', 'city': 'child', 'code': 'Y2rWliOhf8Ir'}, {'age': '18', 'city': 'Boston', 'date': '29/12/1957', 'token': 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c'}, {'name': 'Trans male', 'security related': 'E5_N8G2xWM6D', 'account': 'Please'}, {'place': '[latitude]', 'software': 'Mozilla/5.0 (Macintosh; PPC Mac OS X 10.7.5; rv:12.5) Gecko/20100101 Firefox/12.5.9'}, {'username': 'Carleton', 'age': '18', 'city': '[-38.9302,113.5422]', 'password': 'yZqd7gHyZq91'}, {'time': '10:18 PM', 'role': 'Human Group Coordinator', 'place': 'Cleveland', 'email': 'Emilie_Beatty53@hotmail.com', 'account number': '63652332', 'PIN': '8824', 'EYECOLOR': 'Eye color: Brown'}, {'name': 'Garrick Murray', 'database': '2191941526453503'}, {'name':

In [524]:
len(predicted_labels)

100

In [525]:
print(total_time)

2167.19


In [526]:
print(average_time_per_prompt)

21.67


In [527]:
def get_original_labels(data):
    return data['sensitive_data_json'].tolist()

In [528]:
original_labels = get_original_labels(df_filtered)

In [529]:
len(original_labels)

100

In [530]:
label_comparison = []

In [555]:

# Function to calculate accuracy based on matching labels
def calculate_accuracy_label_comparison(parsed_data, sensitive_data_json_list):
    correct_count = 0
    total_count = 0
    label_comparison = []
    for i, (parsed_item, sensitive_data) in enumerate(zip(parsed_data, sensitive_data_json_list)):
        original_sensitive_values = list(sensitive_data.values())
        print("original values", original_sensitive_values)

        generated_sensitive_values = list(parsed_item.values())  
        print("generated values", generated_sensitive_values)
        label_comparison.append({"actual_values":original_sensitive_values, "predicted_values":generated_sensitive_values})

        label_correct = 0
        for generated_value in generated_sensitive_values:
            for original_value in original_sensitive_values:
                original_value_lower = original_value.lower()
                generated_value_lower = generated_value.lower()
                # original_value_lower = original_value_lower.replace(" ","")
                if original_value_lower in generated_value_lower or generated_value_lower in original_value_lower:
                    label_correct +=1
        if label_correct>0:
            if label_correct>len(original_sensitive_values):
                label_correct = len(original_sensitive_values) #added this for experiment with HF model (generated sensitive values are split)
            print(f"number of correct labels {label_correct}/{len(original_sensitive_values)}")
        else:
            print("0 correct labels found")
            
        correct_count+=label_correct
        total_count += len(original_sensitive_values)
        print()

    accuracy = correct_count / total_count if total_count > 0 else 0
    return accuracy, label_comparison



In [532]:
predicted_labels[0]

{'IMEI': '06-184755-866851-3'}

In [533]:
# Accuracy measure 
accuracy, label_comparison= calculate_accuracy_label_comparison(predicted_labels, original_labels)
print(f"Accuracy: {accuracy * 100:.2f}%")

original values ['06-184755-866851-3', 'Optimization']
generated values ['06-184755-866851-3']
number of correct labels 1/2

original values ['Omer', '78B5R2MVFAHJ48500']
generated values ['Omer', 'license', '78B5R2MVFAHJ48500']
number of correct labels 2/2

original values ['Kattie', '72', 'Intersex person', '158centimeters']
generated values ['72', 'Intersex', '158centimeters']
number of correct labels 3/4

original values ['16356', '5890724654311332']
generated values ['Nancy', '18', 'Boston', '16356', '5890724654311332']
number of correct labels 2/2

original values ['88', '5862', 'Y2rWliOhf8Ir']
generated values ['88', 'child', 'Y2rWliOhf8Ir']
number of correct labels 2/3

original values ['29/12/1957', 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c']
generated values ['18', 'Boston', '29/12/1957', 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c']
number of correct labels 2/2

original values ['Trans male', 'E5_N8G2xWM6D']
generated values ['Trans male', 'E5_N8G2xWM6D', 'Please']
number of cor

In [534]:
print(label_comparison)

[{'actual_values': ['06-184755-866851-3', 'Optimization'], 'predicted_values': ['06-184755-866851-3']}, {'actual_values': ['Omer', '78B5R2MVFAHJ48500'], 'predicted_values': ['Omer', 'license', '78B5R2MVFAHJ48500']}, {'actual_values': ['Kattie', '72', 'Intersex person', '158centimeters'], 'predicted_values': ['72', 'Intersex', '158centimeters']}, {'actual_values': ['16356', '5890724654311332'], 'predicted_values': ['Nancy', '18', 'Boston', '16356', '5890724654311332']}, {'actual_values': ['88', '5862', 'Y2rWliOhf8Ir'], 'predicted_values': ['88', 'child', 'Y2rWliOhf8Ir']}, {'actual_values': ['29/12/1957', 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c'], 'predicted_values': ['18', 'Boston', '29/12/1957', 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c']}, {'actual_values': ['Trans male', 'E5_N8G2xWM6D'], 'predicted_values': ['Trans male', 'E5_N8G2xWM6D', 'Please']}, {'actual_values': ['[-71.6702,-107.6572]', 'Mozilla/5.0 (Macintosh; PPC Mac OS X 10.7.5; rv:12.5) Gecko/20100101 Firefox/12.5.9'], 'pred

In [535]:
def open_results_file(filename):
    if os.path.exists(filename):
        with open(filename, 'r') as file:
            data = json.load(file)
    else:
        data = []
    return data


In [536]:
model_name = "llama3.2:latest"
# model_name = "gemma:2b"

In [537]:
data_with_labels = open_results_file(results_with_labels_file_name)

In [538]:
data_only_results = open_results_file(results_file_name)

In [539]:
print(f"accuracy = {accuracy * 100:.2f}, samples = {samples}, model_name = {model_name}, average_time_per_prompt = {average_time_per_prompt}")

accuracy = 73.48, samples = 100, model_name = llama3.2:latest, average_time_per_prompt = 21.67


In [540]:
accuracy_percent = accuracy*100
accuracy_percent

73.48242811501598

In [541]:
model_name

'llama3.2:latest'

In [542]:
def experiment_results_with_labels(labelcomparison, accuracy, samples, model_name, per_prompt_time, total_time):
    return {"label comparison":labelcomparison, "accuracy":accuracy, "number_of_samples":samples, "model_name":model_name, "average_time_per_prompt":per_prompt_time, "total_time":total_time}

In [543]:
def experiment_results(accuracy, samples, model_name, per_prompt_time, totaltime):
    return {"accuracy":accuracy, "number_of_samples":samples, "model_name":model_name, "average_time_per_prompt":per_prompt_time, "total_time":totaltime}

In [544]:
data_with_labels.append(experiment_results_with_labels(label_comparison, accuracy_percent, samples, model_name, average_time_per_prompt, total_time))

In [545]:
data_only_results.append(experiment_results(accuracy_percent, samples, model_name, average_time_per_prompt, total_time))

In [546]:
experiment_results(accuracy=accuracy_percent, samples=samples, model_name=model_name, per_prompt_time=average_time_per_prompt, totaltime=total_time)

{'accuracy': 73.48242811501598,
 'number_of_samples': 100,
 'model_name': 'llama3.2:latest',
 'average_time_per_prompt': 21.67,
 'total_time': 2167.19}

In [547]:
def dump_data(data,file_name):
    with open(file_name, 'w') as file:
        json.dump(data, file, indent=4)
    print("Experiment results saved successfully!")

In [548]:
dump_data(data_with_labels, results_with_labels_file_name)

Experiment results saved successfully!


In [549]:
dump_data(data_only_results, results_file_name)

Experiment results saved successfully!


### Hugging face experiment

In [45]:
model_name = "Isotonic/deberta-v3-base_finetuned_ai4privacy_v2"

In [649]:
model_name = "Isotonic/mdeberta-v3-base_finetuned_ai4privacy_v2"

In [617]:
model_name

'Isotonic/mdeberta-v3-base_finetuned_ai4privacy_v2'

In [650]:
def run_inference(text):
    gen = pipeline("token-classification", model_name, device=-1, torch_dtype=torch.float32)
    output = gen(text, aggregation_strategy="simple")
    return {item['entity_group']: item['word'] for item in output}


In [651]:
len(df_filtered)

500

In [620]:
import time

In [652]:
def run_hf_experiment(data):
    predicted_label_hf=[]
    average_time = 0
    sum_time = 0
    for sentence in data['source_text']:
        start_time = time.time()
        labels = run_inference(sentence)
        end_time = time.time()
        execution_time = end_time - start_time
        sum_time = sum_time + execution_time
        print(f"Execution Time: {execution_time} seconds")
        predicted_label_hf.append(labels)
    average_time = sum_time / len(data)
    print(f"Average time = {average_time}")
    return predicted_label_hf, average_time, sum_time

In [653]:
predicted_label_hf, average_time_per_prompt, sum_time= run_hf_experiment(df_filtered)

Device set to use cpu
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Execution Time: 1.1256341934204102 seconds


Device set to use cpu
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Execution Time: 1.3189342021942139 seconds


Device set to use cpu
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


...

Execution Time: 1.0944252014160156 seconds


Device set to use cpu
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Execution Time: 1.4062068462371826 seconds


Device set to use cpu
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Execution Time: 1.231750249862671 seconds
Average time = 1.2668695707321167


In [654]:
print(predicted_label_hf)

[{'PHONEIMEI': '06-184755-866851-3.', 'JOBAREA': 'Optimization'}, {'FIRSTNAME': 'Omer', 'VEHICLEVIN': '78B5R2MVFAHJ48500'}, {'FIRSTNAME': 'Kattie', 'GENDER': 'Intersex person', 'HEIGHT': '158centimeters'}, {'ZIPCODE': '16356', 'CREDITCARDNUMBER': '5890724654311332'}, {'AGE': '88', 'BUILDINGNUMBER': '5862,', 'PASSWORD': 'Y2rWliOhf8Ir'}, {'DOB': '29/12/1957', 'IPV6': 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c'}, {'GENDER': 'Trans male', 'PASSWORD': 'E5_N8G2xWM6D'}, {'NEARBYGPSCOORDINATE': '[-71.6702,-107.6572].', 'USERAGENT': 'Mozilla/5.0 (Macintosh; PPC Mac OS X 10.7.5; rv:12.5) Gecko/20100101 Firefox/12.5.9'}, {'FIRSTNAME': 'Carleton', 'NEARBYGPSCOORDINATE': '[-38.9302,113.5422].', 'PASSWORD': 'yZqd7gHyZq91.'}, {'TIME': '10:18 PM', 'JOBTITLE': 'Human Group Coordinator', 'COUNTY': 'Cleveland', 'EMAIL': 'Emilie_Beatty53@hotmail.com', 'ACCOUNTNUMBER': '63652332', 'PIN': '8824', 'EYECOLOR': 'Eye color: Brown'}, {'FIRSTNAME': 'Garrick', 'LASTNAME': 'Leuschke', 'MASKEDNUMBER': '219194152645350

In [655]:
len(predicted_label_hf)

500

In [656]:
print(average_time_per_prompt)

1.2668695707321167


In [657]:
print(sum_time)

633.4347853660583


In [658]:
original_labels_hf = get_original_labels(df_filtered)

In [659]:
len(original_labels_hf)

500

In [660]:
original_labels_hf

[{'PHONEIMEI': '06-184755-866851-3', 'JOBAREA': 'Optimization'},
 {'FIRSTNAME': 'Omer', 'VEHICLEVIN': '78B5R2MVFAHJ48500'},
 {'FIRSTNAME': 'Kattie',
  'AGE': '72',
  'GENDER': 'Intersex person',
  'HEIGHT': '158centimeters'},
 {'BUILDINGNUMBER': '16356', 'MASKEDNUMBER': '5890724654311332'},
 {'AGE': '88', 'BUILDINGNUMBER': '5862', 'PASSWORD': 'Y2rWliOhf8Ir'},
 {'DOB': '29/12/1957', 'IPV6': 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c'},
 {'GENDER': 'Trans male', 'PASSWORD': 'E5_N8G2xWM6D'},
 {'NEARBYGPSCOORDINATE': '[-71.6702,-107.6572]',
  'USERAGENT': 'Mozilla/5.0 (Macintosh; PPC Mac OS X 10.7.5; rv:12.5) Gecko/20100101 Firefox/12.5.9'},
 {'FIRSTNAME': 'Carleton',
  'NEARBYGPSCOORDINATE': '[-38.9302,113.5422]',
  'PASSWORD': 'yZqd7gHyZq91'},
 {'TIME': '10:18 PM',
  'JOBTITLE': 'Human Group Coordinator',
  'COUNTY': 'Cleveland',
  'EMAIL': 'Emilie_Beatty53@hotmail.com',
  'ACCOUNTNUMBER': '63652332',
  'PIN': '8824',
  'EYECOLOR': 'Eye color: Brown'},
 {'FIRSTNAME': 'Garrick',
  'LASTNAME

In [661]:
# Accuracy measure 
accuracy, label_comparison = calculate_accuracy_label_comparison(predicted_label_hf, original_labels_hf)
print(f"Accuracy: {accuracy*100:.2f}%")
print(f"Accuracy: {accuracy}%")

original values ['06-184755-866851-3', 'Optimization']
generated values ['06-184755-866851-3.', 'Optimization']
number of correct labels 2/2

original values ['Omer', '78B5R2MVFAHJ48500']
generated values ['Omer', '78B5R2MVFAHJ48500']
number of correct labels 2/2

original values ['Kattie', '72', 'Intersex person', '158centimeters']
generated values ['Kattie', 'Intersex person', '158centimeters']
number of correct labels 3/4

original values ['16356', '5890724654311332']
generated values ['16356', '5890724654311332']
number of correct labels 2/2

original values ['88', '5862', 'Y2rWliOhf8Ir']
generated values ['88', '5862,', 'Y2rWliOhf8Ir']
number of correct labels 3/3

original values ['29/12/1957', 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c']
generated values ['29/12/1957', 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c']
number of correct labels 2/2

original values ['Trans male', 'E5_N8G2xWM6D']
generated values ['Trans male', 'E5_N8G2xWM6D']
number of correct labels 2/2

original values [

In [663]:
len(label_comparison)

500

In [ ]:
pro

In [662]:
accuracy_percent = accuracy*100
accuracy_percent

84.38516590761223

In [664]:
len(df)

43501

In [665]:
results_with_labels_file_name = 'results_HF_updated.json'

In [666]:
data_with_labels = open_results_file(results_with_labels_file_name)
data_only_results = open_results_file(results_file_name)

print(f"accuracy = {accuracy * 100:.2f}, samples = {len(df_filtered)}, model_name = {model_name}")

accuracy_percent = accuracy*100

data_with_labels.append(experiment_results_with_labels(label_comparison,accuracy_percent, len(df_filtered), model_name, average_time_per_prompt, sum_time))
data_only_results.append(experiment_results(accuracy_percent, len(df_filtered), model_name, average_time_per_prompt, sum_time))

dump_data(data_with_labels, results_with_labels_file_name)
dump_data(data_only_results, results_file_name)
print("Experiment results saved successfully!")

accuracy = 84.39, samples = 500, model_name = Isotonic/mdeberta-v3-base_finetuned_ai4privacy_v2
Experiment results saved successfully!
Experiment results saved successfully!
Experiment results saved successfully!


In [551]:
import json

# Load the JSON data
with open("results_with_labels_hf_fulldata.json", "r") as file:
    data = json.load(file)

# Extract actual and predicted labels
original_labels_hf = [dict(enumerate(item["actual_label"])) for item in data[0]["label comparison"]]
predicted_label_hf = [dict(enumerate(item["predicted_label"])) for item in data[0]["label comparison"]]

# Print the results
print("Original Labels:", original_labels_hf)
print("Predicted Labels:", predicted_label_hf)


Original Labels: [{0: '06-184755-866851-3', 1: 'Optimization'}, {0: 'Omer', 1: '78B5R2MVFAHJ48500'}, {0: 'Kattie', 1: '72', 2: 'Intersex person', 3: '158centimeters'}, {0: '16356', 1: '5890724654311332'}, {0: '88', 1: '5862', 2: 'Y2rWliOhf8Ir'}, {0: '29/12/1957', 1: 'edaf:fd8f:e1e8:cfec:8bab:1afd:6aad:550c'}, {0: 'Trans male', 1: 'E5_N8G2xWM6D'}, {0: '[-71.6702,-107.6572]', 1: 'Mozilla/5.0 (Macintosh; PPC Mac OS X 10.7.5; rv:12.5) Gecko/20100101 Firefox/12.5.9'}, {0: 'Carleton', 1: '[-38.9302,113.5422]', 2: 'yZqd7gHyZq91'}, {0: '10:18 PM', 1: 'Human Group Coordinator', 2: 'Cleveland', 3: 'Emilie_Beatty53@hotmail.com', 4: '63652332', 5: '8824', 6: 'Eye color: Brown'}, {0: 'Garrick', 1: 'Leuschke', 2: '2191941526453503'}, {0: 'Carmen', 1: 'National Brand Architect', 2: 'Usability', 3: '109.4.61.213', 4: '4d36:f8ad:4ebd:1bff:c5eb:62aa:b4d7:dddf'}, {0: 'Stephen', 1: '10/03/1976', 2: '4:40 AM', 3: 'S Broadway', 4: '61915', 5: 'Port Diegostead', 6: '[-56.5612,-68.9245]'}, {0: 'Ms.', 1: 'Nort

In [553]:
len(predicted_label_hf)

43501

In [552]:
len(original_labels_hf)

43501

### old code below

In [51]:

def calculate_accuracy_full_comparison(parsed_data, sensitive_data_json_list):
    correct_count = 0
    total_count = len(sensitive_data_json_list)

    for i, (parsed_item, sensitive_data) in enumerate(zip(parsed_data, sensitive_data_json_list)):
        original_sensitive_values = list(sensitive_data.values())
        print("original values", original_sensitive_values)

        generated_sensitive_values = list(parsed_item.values())  
        print("generated values", generated_sensitive_values)

        is_correct = True
        for original_value in original_sensitive_values:
            if not any(original_value in generated_value for generated_value in generated_sensitive_values):
                is_correct = False
                break

        if is_correct:
            print("MATCH!")
            correct_count += 1
        else:
            print("Not Match")
        
        # Update total count of values to calculate accuracy
        # total_count += len(original_sensitive_values)

    # Calculate accuracy: score / total values
    accuracy = correct_count / total_count if total_count > 0 else 0
    return accuracy